[View in Colaboratory](https://colab.research.google.com/github/grommy/Wooey/blob/master/First_steps_in_ML_%232_TensorFlow.ipynb)

Додаток до 2ї статті  "Вступ до Машинного Навчання" на ДОУ: https://dou.ua/lenta/articles/introduction-machine-learning-2/

Посилання на цю сторінку: http://bit.ly/ml-introduction-2-colab

Пояснення до блоків коду нижче дивитися в статті.

Пояснення як користуватися Colaboratory залишене поза даною статтею. Для ознайомлення (англійською) дивитися тут: https://colab.research.google.com/notebooks/welcome.ipynb

Уточнюючі запитання можна задавати в коментарях під статтею.


In [1]:
#@title Виконай мене. Цей блок завантажує бібліотики, імпортує модулі і визначає функції для візуалізації, в рамках статті не обовязково розбиратися з вмістом цього блоку.

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import collections

import numpy as np
import pandas as pd

import tensorflow as tf
print('This code requires TensorFlow v1.3+')
print('You have:', tf.__version__)

!pip install -q xgboost==0.4a30
import xgboost as xgb

!git clone https://github.com/PAIR-code/facets
!jupyter nbextension install facets/facets-dist/ 

import sys
import os

sys.path.append(os.path.abspath('./facets/facets_overview/python/'))

tf.logging.set_verbosity(tf.logging.ERROR)


from generic_feature_statistics_generator import GenericFeatureStatisticsGenerator
import base64

class FacetsOverview(object):
  def __init__(self, df_train, df_test):
    gfsg = GenericFeatureStatisticsGenerator()
    self._proto = gfsg.ProtoFromDataFrames([{'name': 'train', 'table': df_train},
                                      {'name': 'test', 'table': df_test}])
  
  def _repr_html_(self):
    protostr = base64.b64encode(self._proto.SerializeToString()).decode("utf-8")

    HTML_TEMPLATE = """<link rel="import" href="/nbextensions/facets-dist/facets-jupyter.html" >
            <facets-overview id="elem"></facets-overview>
            <script>
              document.querySelector("#elem").protoInput = "{protostr}";
            </script>"""
    html = HTML_TEMPLATE.format(protostr=protostr)
    return html
  
class FacetsDive(object):
  def __init__(self, data):
    self._data = data
    self.height = 1000
    
  def _repr_html_(self):
    HTML_TEMPLATE = """<link rel="import" href="/nbextensions/facets-dist/facets-jupyter.html" >
        <facets-dive id="elem" height="{height}"></facets-dive>
        <script>
          document.querySelector("#elem").data = {data};
        </script>"""
    html = HTML_TEMPLATE.format(data=self._data.to_json(orient='records'), height=self.height)
    return html


This code requires TensorFlow v1.3+
You have: 1.9.0
You are using pip version 10.0.1, however version 18.0 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
Cloning into 'facets'...
remote: Counting objects: 900, done.
remote: Compressing objects: 100% (33/33), done.
remote: Total 900 (delta 21), reused 14 (delta 7), pack-reused 860
Receiving objects: 100% (900/900), 17.44 MiB | 22.18 MiB/s, done.
Resolving deltas: 100% (530/530), done.
Making directory: /usr/local/share/jupyter/nbextensions/facets-dist/
Copying: /content/facets/facets-dist/facets-jupyter.html -> /usr/local/share/jupyter/nbextensions/facets-dist/facets-jupyter.html

    To initialize this nbextension in the browser every time the notebook (or other app) loads:
    
          jupyter nbextension enable <the entry point>
    


In [0]:
# Імпортування модулів необхідних для роботи
from google.colab import files
import numpy as np
import pandas as pd
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.ERROR)

In [3]:
# Завантажуємо файл з результатами тестування
!mkdir drive
!wget 'https://drive.google.com/uc?id=1nlTTlDYQKnhBDYsf0OIkGysZxjadWeTv&export=download' -O drive/exams.csv

--2018-07-24 14:29:36--  https://drive.google.com/uc?id=1nlTTlDYQKnhBDYsf0OIkGysZxjadWeTv&export=download
Resolving drive.google.com (drive.google.com)... 74.125.197.100, 74.125.197.113, 74.125.197.101, ...
Connecting to drive.google.com (drive.google.com)|74.125.197.100|:443... connected.
HTTP request sent, awaiting response... 302 Moved Temporarily
Location: https://doc-08-5c-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/cv5tq46ldt8i2h65bjlgc0g9lrmmuept/1532440800000/01333786639642341364/*/1nlTTlDYQKnhBDYsf0OIkGysZxjadWeTv?e=download [following]
--2018-07-24 14:29:36--  https://doc-08-5c-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/cv5tq46ldt8i2h65bjlgc0g9lrmmuept/1532440800000/01333786639642341364/*/1nlTTlDYQKnhBDYsf0OIkGysZxjadWeTv?e=download
Resolving doc-08-5c-docs.googleusercontent.com (doc-08-5c-docs.googleusercontent.com)... 74.125.197.132, 2607:f8b0:400e:c03::84
Connecting to doc-08-5c-docs.googleusercontent.com (doc-08

In [4]:
# Зачитуємо дані з файлу
exams = pd.read_csv('drive/exams.csv')

# Виведемо 15 верхніх рядків
exams.head(15)

year    name               subject  test1  test2  exam
0   2017  Андрій            Астрономія     27     47    47
1   2017  Андрій             Економіка     34     54    54
2   2017  Андрій                 Право     26     46    46
3   2017  Андрій            Педагогіка     34     54    54
4   2017  Андрій       Англійська мова     38     58    58
5   2017  Андрій               Історія     25     45    45
6   2017  Андрій             Філософія     41     61    61
7   2017  Андрій            Психологія     33     53    53
8   2017  Андрій            Соціологія     34     54    54
9   2017  Андрій         Правознавство     40     60    60
10  2017  Андрій  Прикладна математика     31     51    51
11  2017  Андрій    Обчислювані методи     37     57    57
12  2017     Аня            Астрономія     50     70    70
13  2017     Аня             Економіка     58     78    77
14  2017     Аня                 Право     51     71    69

In [0]:
# Ділимо набір даних на 3 частини - 1) набір для тренування (60%) 2) набір для оцінки (20%) 3) набір ратифікації (20%)

def split_data(data):
  training = []
  evaluation = []
  validation = []
  for (index, row) in enumerate(data.values):
    ind = index % 10
    if ind < 6:
      training.append(row)
    elif ind < 8:
      evaluation.append(row)
    else:
      validation.append(row)
  return (pd.DataFrame(training, columns=data.columns), 
          pd.DataFrame(evaluation, columns=data.columns), 
          pd.DataFrame(validation, columns=data.columns))
      
training_data, evaluation_data, validation_data = split_data(exams)



In [6]:
# Глянемо в середину набору для тренування

FacetsDive(training_data)

In [7]:
# Візуалізуємо статистику

FacetsOverview(training_data, evaluation_data)

In [8]:
# Підготуємо вхідні дані

input_columns = ['name', 'subject', 'test1', 'test2']
outcome_column = 'failed'

training_data[outcome_column] = training_data['exam'] <= 50 # True = завалений екзамен
evaluation_data[outcome_column] = evaluation_data['exam'] <= 50

train_input = tf.estimator.inputs.pandas_input_fn(
      x=training_data[input_columns], # Вхідні колонки.
      y=training_data[outcome_column], # Вихідна колонка - те що ми передбачаємо.
      batch_size=50,
      num_epochs=None,
      shuffle=False)

# Визначення вхідних колонок для моделі, тут ми вказуємо тип кожної колонки
input_column_defs = [
    tf.feature_column.categorical_column_with_hash_bucket('name', 20),
    tf.feature_column.categorical_column_with_hash_bucket('subject', 20),
    tf.feature_column.numeric_column('test1'),
    tf.feature_column.numeric_column('test2'),
  ]

# Будуємо лінійний класифікатор
classifier = tf.estimator.LinearClassifier(input_column_defs,
  n_classes=2,
  optimizer=tf.train.AdagradOptimizer(
      learning_rate=0.2,)
)

# Тренуємо модель
classifier.train(train_input, steps=500)

# Оцінюємо його на наборі даних для оцінки
eval_input = tf.estimator.inputs.pandas_input_fn(
        x=evaluation_data[input_columns],
        y=evaluation_data[outcome_column], 
        num_epochs=1,
        shuffle=False)

classifier.evaluate(eval_input)

{'accuracy': 0.92771083,
 'accuracy_baseline': 0.77710843,
 'auc': 0.98397243,
 'auc_precision_recall': 0.9539273,
 'average_loss': 0.17726704,
 'global_step': 500,
 'label/mean': 0.22289157,
 'loss': 14.713165,
 'precision': 1.0,
 'prediction/mean': 0.1676192,
 'recall': 0.6756757}

In [9]:
# Пора написати функцію яка використає побудований класифікатор для оцінки ймовірності завалу екзамену
def predict_exam_failure(name, subject, test1, test2):
  # Пакуємо вхідні дані в DataFrame
  data = pd.DataFrame(data={'name': [name], 'subject': [subject], 'test1': [test1], 'test2': [test2]})

  data_input = tf.estimator.inputs.pandas_input_fn(
    x=data,
    shuffle=False)

  predictions = classifier.predict(data_input)
  the_prediction = next(predictions)  # Витягуємо єдиний запис
  return the_prediction['probabilities'][1] # probabilities буде мати два значення - ймовірність False і ймовірність True - в сумі вони мають давати 1.
  # Нас цікавить ймовірність True - провалу екзамену.
 
# Спробуємо на кількох прикладах
print('Андрій', predict_exam_failure('Андрій', 'Право', 50, 50))
print('Аня', predict_exam_failure('Аня', 'Право', 50, 50))

Андрій 0.2969804
Аня 0.08071019
